In [1]:
%%capture

!pip install monai-weekly

# Libraries

In [2]:
import pandas as pd
import numpy as np

from tqdm.notebook import tqdm
import datatable as dt
import datetime
import string
import random
import glob
import time
import os
import gc

from scipy.stats import rankdata

from sklearn.model_selection import StratifiedKFold
from sklearn.preprocessing import StandardScaler
from sklearn.metrics import roc_auc_score
from sklearn.preprocessing import LabelEncoder

import pytorch_lightning as pl
from pytorch_lightning.callbacks import EarlyStopping, LearningRateMonitor, ModelCheckpoint
from pytorch_lightning.utilities.model_summary import ModelSummary
from pytorch_lightning.loggers import TensorBoardLogger

import torch
from torch import nn
from torch.nn import functional as F
from torch.optim import AdamW
from torch.optim.lr_scheduler import ReduceLROnPlateau
from torch.utils.data import TensorDataset, DataLoader

from monai.metrics import ROCAUCMetric

import matplotlib.pyplot as plt
import seaborn as sns

import warnings
warnings.simplefilter('ignore')

# Parameters

In [3]:
class CFG:
    input = "../input/tabular-playground-series-may-2022"
    target = 'target'
    
    n_splits = 10
    seed = 42

    batch_size = 4096
    workers = 4
    epochs = 200
    learning_rate = 1e-2
    
    factor = 0.8
    min_lr = 1e-6
    
    lr_patience = 5
    es_patience = 20

    pred = 'pred'
    test_pred = [f'pred_{i}' for i in range(n_splits)]
    
    model_path = "models"
    tb_log_name = "lightning_logs"

In [4]:
def seed_everything(seed=42):
    random.seed(seed)
    os.environ['PYTHONHASHSEED'] = str(seed)
    np.random.seed(seed)
    pl.utilities.seed.seed_everything(seed, workers=True)
    torch.manual_seed(seed)
    torch.cuda.manual_seed(seed)
    torch.backends.cudnn.deterministic = True
    
seed_everything(CFG.seed)

# Data loading ...

In [5]:
%%time

train = pd.read_csv("/".join([CFG.input, "train.csv"]))
test = pd.read_csv("/".join([CFG.input, "test.csv"]))
submission = pd.read_csv("/".join([CFG.input, "sample_submission.csv"]))

CPU times: user 7.63 s, sys: 836 ms, total: 8.47 s
Wall time: 12.9 s


# Feature engineering

In [6]:
all_df = pd.concat([train, test]).reset_index(drop=True)

In [7]:
class feature_engineering:
    def __init__(self, df):
        self.df = df
        self.f_27_len = len(self.df['f_27'][0])
        self.alphabet_upper = list(string.ascii_uppercase)    
        
    def get_features(self):
        for i in range(self.f_27_len):
            self.df[f'f_27_{i}'] = self.df['f_27'].apply(lambda x: x[i])

        for letter in tqdm(self.alphabet_upper):
            self.df[f'f_27_{letter}_count'] = self.df['f_27'].str.count(letter)

        self.df['f_27_nunique'] = self.df['f_27'].apply(lambda x: len(set(x)))

        return self.df
    
    def scaling(self, features):
        sc = StandardScaler()
        self.df[features] = sc.fit_transform(self.df[features])

        return self.df

    def label_encoding(self, features):
        new_features = []
        
        for feature in features:
            if self.df[feature].dtype == 'O':
                le = LabelEncoder()
                self.df[f'{feature}_enc'] = le.fit_transform(self.df[feature])
                new_features += [f'{feature}_enc']
            else:
                new_features += [feature]

        return self.df, new_features

In [8]:
%%time

fe = feature_engineering(all_df)
all_df = fe.get_features()

  0%|          | 0/26 [00:00<?, ?it/s]

CPU times: user 36.3 s, sys: 321 ms, total: 36.6 s
Wall time: 36.7 s


In [9]:
features = [col for col in all_df.columns if CFG.target not in col]
num_features = []
cat_features = []

for feature in features:
    if all_df[feature].dtype == float:
        num_features.append(feature)
    else:
        cat_features.append(feature)

cat_features.remove('id')
cat_features.remove('f_27')

# Scaling and encoding

In [10]:
all_df = fe.scaling(num_features)
all_df, cat_features = fe.label_encoding(cat_features)

all_features = cat_features + num_features

In [11]:
train_len = train.shape[0]
train = all_df[:train_len]
test = all_df[train_len:].reset_index(drop=True)

# Check data

In [12]:
display(train[all_features])
display(test[all_features])

f_07  f_08  f_09  f_10  f_11  f_12  f_13  f_14  f_15  f_16  ...  \
0          1     5     1     3     3     3     1     6     1     0  ...   
1          1     3     4     0     2     3     0     1     0     4  ...   
2          1     0     2     6     6     4     3     1     2     2  ...   
3          3     2     1     0     1     6     4     2     3     3  ...   
4          3     3     0     4     3     0     6     0     3     3  ...   
...      ...   ...   ...   ...   ...   ...   ...   ...   ...   ...  ...   
899995     2     1     2     0     0     5     3     0     2     0  ...   
899996     4     1     2     4     3     1     4     1     2     2  ...   
899997     0     0     6     4     1     3     1     2     3     2  ...   
899998     0     2     2     2     2     2     1     2     2     2  ...   
899999     7     1     4     2     0     2     0     5     3     7  ...   

            f_06      f_19      f_20      f_21      f_22      f_23      f_24  \
0       0.112443 -0.004261 -0.309692  1.293554 -1.033547  0.463713 -1.000409   
1       0.447214 -1.492413 -0.374592  0.939560  0.932736 -0.107252 -0.366544   
2      -0.709543  1.085122 -1.378981 -0.253157 -0.562295 -0.061146  0.139340   
3      -0.283358  0.333830 -0.801679 -0.880887  0.236763 -0.522878  0.849260   
4       0.406895 -0.187542  0.325785  0.518794 -1.593431 -0.432033  1.034205   
...          ...       ...       ...       ...       ...       ...       ...   
899995  1.310290 -1.887008 -1.028186 -0.812476 -0.647559  0.363865  0.492034   
899996 -1.799597 -0.876710  0.382783 -2.026714  0.988057 -0.124081 -0.029429   
899997 -1.046748 -0.679712  0.586258 -0.485639 -0.058859 -1.708156 -0.379977   
899998 -0.059322  0.314036  1.095060 -0.975071  0.992044  1.011215  0.378216   
899999 -0.214860  1.366434  0.556632 -0.183877  0.550166  1.684800  0.895788   

            f_25      f_26      f_28  
0      -0.158744  0.406330  0.282882  
1      -1.637310 -0.167694  1.578761  
2       1.080993 -1.639444 -0.819221  
3      -1.120560 -0.389873  0.882558  
4      -1.440633  1.620807 -0.909715  
...          ...       ...       ...  
899995  1.050209  0.376731  1.905100  
899996 -0.085212 -1.413568  0.563819  
899997  0.669362  0.765789 -0.416986  
899998 -0.961912  0.267673  0.200034  
899999 -0.243411  0.699874 -0.186788  

[900000 rows x 67 columns]

f_07  f_08  f_09  f_10  f_11  f_12  f_13  f_14  f_15  f_16  ...  \
0          6     6     0     0     0     5     1     1     2     2  ...   
1          1     3     4     0     2     1     3     0     0     0  ...   
2          3     3     4     1     1     3     2     2     4     1  ...   
3          0     0     4     2     1     5     0     3     3     1  ...   
4          2     2     2     0     0     3     0     1     2     0  ...   
...      ...   ...   ...   ...   ...   ...   ...   ...   ...   ...  ...   
699995     0     1     6     2     5     3     4     2     2     3  ...   
699996     4     3     4     2     0     2     3     2     2     3  ...   
699997     1     1     2     1     1     3     1     0     1     3  ...   
699998     5     1     1     3     0     2     4     2     4     6  ...   
699999     0     3     4     3     1     3     1     5     1     1  ...   

            f_06      f_19      f_20      f_21      f_22      f_23      f_24  \
0       0.501289 -0.620353  1.219482 -0.342578 -0.483998 -0.841876 -0.873431   
1      -0.191672 -2.043657  0.524057  1.021410  0.064108  0.918805 -1.049862   
2       1.358225 -0.791152 -0.512660 -2.765496  0.538571 -1.951289  0.860973   
3       1.118767 -0.739645  1.328568 -0.176802 -1.604263  0.866319 -0.846870   
4       1.784686 -0.983181  0.115548  0.096671 -0.399071  0.097876 -1.346862   
...          ...       ...       ...       ...       ...       ...       ...   
699995  0.534835  0.197408 -0.837110  1.110621  0.461287  0.362271  0.664070   
699996 -0.053392 -0.519600 -0.026217  1.282008  0.568114 -0.311928  1.392300   
699997 -0.969225 -0.056144 -0.310905  1.681052 -0.749778  0.597855 -1.002033   
699998 -0.708357  1.613016 -1.210043  0.647674 -0.689121  0.566459  0.969731   
699999  0.891482  1.724761 -0.813502 -1.366003 -1.761695 -1.894229  0.248389   

            f_25      f_26      f_28  
0      -0.886319  2.171056  0.416324  
1      -0.372617  1.145528 -0.276538  
2       0.169406 -0.117138 -0.366193  
3      -0.487693  1.427704 -1.178037  
4       0.428238  0.607594  0.107105  
...          ...       ...       ...  
699995  0.165302 -0.113313  0.854756  
699996 -0.698034  0.754291 -0.409275  
699997 -2.093934 -1.052084  0.546731  
699998 -0.218685 -1.490039 -1.526961  
699999 -1.411361 -0.290335 -0.650970  

[700000 rows x 67 columns]

In [13]:
display(train[train[all_features].isna().any(axis=1)])
display(test[test[all_features].isna().any(axis=1)])

Empty DataFrame
Columns: [id, f_00, f_01, f_02, f_03, f_04, f_05, f_06, f_07, f_08, f_09, f_10, f_11, f_12, f_13, f_14, f_15, f_16, f_17, f_18, f_19, f_20, f_21, f_22, f_23, f_24, f_25, f_26, f_27, f_28, f_29, f_30, target, f_27_0, f_27_1, f_27_2, f_27_3, f_27_4, f_27_5, f_27_6, f_27_7, f_27_8, f_27_9, f_27_A_count, f_27_B_count, f_27_C_count, f_27_D_count, f_27_E_count, f_27_F_count, f_27_G_count, f_27_H_count, f_27_I_count, f_27_J_count, f_27_K_count, f_27_L_count, f_27_M_count, f_27_N_count, f_27_O_count, f_27_P_count, f_27_Q_count, f_27_R_count, f_27_S_count, f_27_T_count, f_27_U_count, f_27_V_count, f_27_W_count, f_27_X_count, f_27_Y_count, f_27_Z_count, f_27_nunique, f_27_0_enc, f_27_1_enc, f_27_2_enc, f_27_3_enc, f_27_4_enc, f_27_5_enc, f_27_6_enc, f_27_7_enc, f_27_8_enc, f_27_9_enc]
Index: []

[0 rows x 80 columns]

Empty DataFrame
Columns: [id, f_00, f_01, f_02, f_03, f_04, f_05, f_06, f_07, f_08, f_09, f_10, f_11, f_12, f_13, f_14, f_15, f_16, f_17, f_18, f_19, f_20, f_21, f_22, f_23, f_24, f_25, f_26, f_27, f_28, f_29, f_30, target, f_27_0, f_27_1, f_27_2, f_27_3, f_27_4, f_27_5, f_27_6, f_27_7, f_27_8, f_27_9, f_27_A_count, f_27_B_count, f_27_C_count, f_27_D_count, f_27_E_count, f_27_F_count, f_27_G_count, f_27_H_count, f_27_I_count, f_27_J_count, f_27_K_count, f_27_L_count, f_27_M_count, f_27_N_count, f_27_O_count, f_27_P_count, f_27_Q_count, f_27_R_count, f_27_S_count, f_27_T_count, f_27_U_count, f_27_V_count, f_27_W_count, f_27_X_count, f_27_Y_count, f_27_Z_count, f_27_nunique, f_27_0_enc, f_27_1_enc, f_27_2_enc, f_27_3_enc, f_27_4_enc, f_27_5_enc, f_27_6_enc, f_27_7_enc, f_27_8_enc, f_27_9_enc]
Index: []

[0 rows x 80 columns]

In [14]:
gc.collect()

147

# Network implementation

In [15]:
class Model(pl.LightningModule):
    def __init__(self, in_size, learning_rate, num_targets=1, hidden_size=128):
        super().__init__()
        self.in_size = in_size
        self.lr = learning_rate
        self.num_targets = num_targets
        self.hidden_size = hidden_size
        
        self.fc1 = nn.Linear(self.in_size, self.hidden_size)
        self.fc2 = nn.Linear(self.hidden_size, self.hidden_size)
        self.fc3 = nn.Linear(self.hidden_size, 16)
        self.fc4 = nn.Linear(16, self.num_targets)
        self.relu = F.relu
        self.swish = F.hardswish
        self.flatten = nn.Flatten()
        self.dropout = nn.Dropout(0.2)
        self.roc_auc_metric = ROCAUCMetric()
    
    def forward(self, x):
        x = self.flatten(x)
        x = self.swish(self.fc1(x))
        x = self.swish(self.fc2(x))
        x = self.relu(self.fc2(x))
        x = self.swish(self.fc2(x))
        x = self.fc3(x)
        x = torch.sigmoid(self.fc4(x))
        
        return x
    
    def training_step(self, batch, batch_idx):
        X, y = batch
        y_hat = self(X).squeeze(1)
        loss = F.binary_cross_entropy(y_hat, y)  
        self.log('loss', loss)
        return {'loss': loss}
        
    def validation_step(self, batch, batch_idx):
        X, y = batch
        y_hat = self(X).squeeze(1)
        self.roc_auc_metric(y_hat, y)      
    
    def validation_epoch_end(self, training_step_outputs):
        roc_auc = self.roc_auc_metric.aggregate()
        self.roc_auc_metric.reset()
        self.log('val_auc', roc_auc, prog_bar=True, on_epoch=True)
        
    def predict_step(self, X, batch_idx: int, dataloader_idx: int = None):
        return self(X[0])    
    
    def configure_optimizers(self):
        optimizer = AdamW(
            self.parameters(),
            lr=self.lr,
            eps=1e-8,
            weight_decay=1e-6,
            amsgrad=False
        )
        lr_scheduler = {
            "scheduler": ReduceLROnPlateau(
                optimizer,
                mode='min',
                factor=CFG.factor,
                patience=CFG.lr_patience,
                min_lr=CFG.min_lr
            ),
            "interval": "epoch",
            "frequency": 1,
            "monitor": "val_auc",
            "strict": True,
            "name": "Learning Rate",
        }
        return [optimizer], [lr_scheduler]

In [16]:
skf = StratifiedKFold(n_splits=CFG.n_splits, shuffle=True, random_state=CFG.seed)

for fold, (trn_idx, val_idx) in enumerate(skf.split(train, train[CFG.target])):
    print('Fold:', fold)
    X_train, y_train = train[all_features].iloc[trn_idx], train[CFG.target].iloc[trn_idx]
    X_valid, y_valid = train[all_features].iloc[val_idx], train[CFG.target].iloc[val_idx]
    X_test = test[all_features]
    
    train_ds = TensorDataset(torch.FloatTensor(X_train.values), torch.FloatTensor(y_train.values))
    valid_ds = TensorDataset(torch.FloatTensor(X_valid.values), torch.FloatTensor(y_valid.values))

    train_dl = DataLoader(train_ds, batch_size=CFG.batch_size, shuffle=True, num_workers=CFG.workers)
    valid_dl = DataLoader(valid_ds, batch_size=CFG.batch_size, shuffle=False, num_workers=CFG.workers)

    model = Model(in_size=X_train.shape[1],
                  learning_rate=CFG.learning_rate,
                  num_targets=1,
                  hidden_size=64,
                 )
    #print(ModelSummary(model))
    
    checkpoint_callback = ModelCheckpoint(
        dirpath=CFG.model_path,
        filename=f'model_{fold}_' + '{val_auc:.6f}',
        monitor='val_auc',
        mode='max',
        save_weights_only=True)

    logger = TensorBoardLogger(
        save_dir=os.getcwd(),
        version=fold,
        name=CFG.tb_log_name
    )
 
    early_stop_callback = EarlyStopping(
        monitor='loss',
        min_delta=0.00,
        patience=CFG.es_patience,
        verbose=False,
        mode='min'
    )
    
    lr_monitor = LearningRateMonitor(
        logging_interval='step'
    )
    
    trainer = pl.Trainer(
        fast_dev_run=False,
        max_epochs=CFG.epochs,
        gpus=1,
        precision=32,
        limit_train_batches=1.0,
        limit_val_batches=1.0, 
        num_sanity_val_steps=0,
        val_check_interval=1.0, 
        callbacks=[checkpoint_callback, lr_monitor, early_stop_callback],
        logger=logger
     )

    trainer.fit(model, train_dl, valid_dl)
    trainer.validate(model, valid_dl, verbose=True)

    preds = trainer.predict(model, valid_dl)
    train.loc[val_idx, CFG.pred] = torch.cat(preds).cpu().numpy().flatten()
    
    test_ds = TensorDataset(torch.FloatTensor(X_test.values))
    test_dl = DataLoader(test_ds, batch_size=CFG.batch_size, shuffle=False, num_workers=CFG.workers)

    preds = trainer.predict(model, test_dl)
    test[CFG.test_pred[fold]] = torch.cat(preds).cpu().numpy().flatten()

    del model, trainer, X_train, X_valid, y_train, y_valid, train_ds, valid_ds, train_dl, valid_dl
    gc.collect()
    torch.cuda.empty_cache()
    
auc = roc_auc_score(train[CFG.target], train[CFG.pred])
print(f"auc: {auc:.6f}")

Fold: 0


Training: 0it [00:00, ?it/s]

Validation: 0it [00:00, ?it/s]

Validation: 0it [00:00, ?it/s]

Validation: 0it [00:00, ?it/s]

...

Validation: 0it [00:00, ?it/s]

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━━━━┓
┃      Validate metric      ┃       DataLoader 0        ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━━━━┩
│          val_auc          │    0.9965873629055232     │
└───────────────────────────┴───────────────────────────┘

Predicting: 198it [00:00, ?it/s]

Predicting: 198it [00:00, ?it/s]

auc: 0.996564


# Submission

In [17]:
models = np.sort(glob.glob(f"./{CFG.model_path}/*.ckpt"))
trainer = pl.Trainer(gpus=1)

for model_name in models:
    X_test = test[all_features]
    model = Model(in_size=X_test.shape[1],
              learning_rate=CFG.learning_rate,
              num_targets=1,
              hidden_size=64,
             )
    model.load_state_dict(torch.load(model_name)['state_dict'])
    test_ds = TensorDataset(torch.FloatTensor(X_test.values))
    test_dl = DataLoader(test_ds, batch_size=CFG.batch_size, shuffle=False, num_workers=CFG.workers)
    
    preds = trainer.predict(model, test_dl)
    test[CFG.test_pred[fold]] = torch.cat(preds).cpu().numpy().flatten()
    
submission[CFG.target] = test[CFG.test_pred].mean(axis=1)
submission.to_csv("submission.csv", index=False)
submission

Predicting: 0it [00:00, ?it/s]

Predicting: 0it [00:00, ?it/s]

Predicting: 0it [00:00, ?it/s]

Predicting: 0it [00:00, ?it/s]

Predicting: 0it [00:00, ?it/s]

...

Predicting: 0it [00:00, ?it/s]

Predicting: 0it [00:00, ?it/s]

Predicting: 0it [00:00, ?it/s]

Predicting: 0it [00:00, ?it/s]

id        target
0        900000  9.999930e-01
1        900001  9.999525e-01
2        900002  1.405871e-09
3        900003  1.939269e-05
4        900004  9.996497e-01
...         ...           ...
699995  1599995  6.552715e-01
699996  1599996  9.999081e-01
699997  1599997  9.186254e-02
699998  1599998  6.275649e-07
699999  1599999  1.270899e-06

[700000 rows x 2 columns]